<img src='http://hilpisch.com/tpq_logo.png' width="350px" align="right">

# Reinforcement Learning

**OLS Regression & Efficient Markets**

&copy; Dr. Yves J. Hilpisch | The Python Quants GmbH

<a href="mailto:training@tpq.io">training@tpq.io</a> | https://cpf.tpq.io | [@dyjh](https://twitter.com/dyjh) | [YouTube](https://youtube.com/@dyjh)

<img src="https://certificate.tpq.io/rl4finance_cover_bw.png" width="300px" align="left">

## Imports

In [1]:
import math
import cufflinks
import numpy as np
import pandas as pd
from pylab import plt
plt.style.use('seaborn-v0_8')
cufflinks.set_config_file(offline=True)

## Random Walks

Eugene F. Fama (1965): “Random Walks in Stock Market Prices”:

> “For many years, economists, statisticians, and teachers of finance have been interested in developing and testing models of stock price behavior. One important model that has evolved from this research is the theory of random walks. This theory casts serious doubt on many other methods for describing and predicting stock price behavior—methods that have considerable popularity outside the academic world. For example, we shall see later that, if the random-walk theory is an accurate description of reality, then the various “technical” or “chartist” procedures for predicting stock prices are completely without value.”

Michael Jensen (1978): “Some Anomalous Evidence Regarding Market Efficiency”:

>“A market is efficient with respect to an information set S if it is impossible to make economic profits by trading on the basis of information set S.”

If a stock price follows a (simple) random walk (no drift & normally distributed returns), then it rises and falls with the same probability of 50% (“toss of a coin”).

**In such a case, the best predictor of tomorrow’s stock price — in a least-squares sense — is today’s stock price.**

### Retrieving Cross-Asset Data

In [2]:
url = 'https://certificate.tpq.io/rl4finance.csv'

In [3]:
data = pd.read_csv(url, index_col=0, parse_dates=True)

In [4]:
data.dropna(inplace=True)

In [5]:
data.head()

AAPL.O  MSFT.O  INTC.O   AMZN.O    GS.N     .SPX   .VIX  \
Date                                                                     
2014-01-02  19.754623   37.16  25.790  19.8985  176.89  1831.98  14.23   
2014-01-03  19.320695   36.91  25.780  19.8220  178.15  1831.37  13.76   
2014-01-06  19.426052   36.13  25.460  19.6815  179.37  1826.77  13.55   
2014-01-07  19.287034   36.41  25.585  19.9015  178.29  1837.88  12.92   
2014-01-08  19.409266   35.76  25.430  20.0960  178.44  1837.49  12.87   

                SPY    EUR=     XAU=    GDX     GLD  
Date                                                 
2014-01-02  182.920  1.3670  1224.51  22.03  118.00  
2014-01-03  182.885  1.3587  1236.16  21.83  119.29  
2014-01-06  182.360  1.3627  1237.59  21.93  119.50  
2014-01-07  183.480  1.3615  1231.49  21.97  118.82  
2014-01-08  183.520  1.3574  1225.71  21.61  118.12

In [13]:
data.tail()  # 10 years of data from 2014 BoY to 2023 EoY

AAPL.O  MSFT.O  INTC.O  AMZN.O    GS.N     .SPX   .VIX     SPY  \
Date                                                                         
2023-12-22  193.60  374.58   48.00  153.42  380.65  4754.63  13.03  473.65   
2023-12-26  193.05  374.66   50.50  153.41  381.61  4774.75  12.99  475.65   
2023-12-27  193.15  374.07   50.76  153.34  384.48  4781.58  12.43  476.51   
2023-12-28  193.58  375.28   50.39  153.38  386.41  4783.35  12.47  476.69   
2023-12-29  192.53  376.04   50.25  151.94  385.77  4769.83  12.45  475.31   

              EUR=       XAU=    GDX     GLD  
Date                                          
2023-12-22  1.1010  2052.9751  31.56  190.27  
2023-12-26  1.1042  2066.6050  31.67  191.72  
2023-12-27  1.1103  2077.1589  31.98  192.59  
2023-12-28  1.1059  2064.8601  31.17  191.47  
2023-12-29  1.1036  2062.5900  31.01  191.17

In [14]:
data.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 2516 entries, 2014-01-02 to 2023-12-29
Data columns (total 12 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   AAPL.O  2516 non-null   float64
 1   MSFT.O  2516 non-null   float64
 2   INTC.O  2516 non-null   float64
 3   AMZN.O  2516 non-null   float64
 4   GS.N    2516 non-null   float64
 5   .SPX    2516 non-null   float64
 6   .VIX    2516 non-null   float64
 7   SPY     2516 non-null   float64
 8   EUR=    2516 non-null   float64
 9   XAU=    2516 non-null   float64
 10  GDX     2516 non-null   float64
 11  GLD     2516 non-null   float64
dtypes: float64(12)
memory usage: 255.5 KB


### Calculating the Log Returns

In [9]:
rets = np.log(data / data.shift(1))

In [10]:
rets.head()

AAPL.O    MSFT.O    INTC.O    AMZN.O      GS.N      .SPX  \
Date                                                                     
2014-01-02       NaN       NaN       NaN       NaN       NaN       NaN   
2014-01-03 -0.022211 -0.006750 -0.000388 -0.003852  0.007098 -0.000333   
2014-01-06  0.005438 -0.021359 -0.012490 -0.007113  0.006825 -0.002515   
2014-01-07 -0.007182  0.007720  0.004898  0.011116 -0.006039  0.006063   
2014-01-08  0.006318 -0.018014 -0.006077  0.009726  0.000841 -0.000212   

                .VIX       SPY      EUR=      XAU=       GDX       GLD  
Date                                                                    
2014-01-02       NaN       NaN       NaN       NaN       NaN       NaN  
2014-01-03 -0.033587 -0.000191 -0.006090  0.009469 -0.009120  0.010873  
2014-01-06 -0.015379 -0.002875  0.002940  0.001156  0.004570  0.001759  
2014-01-07 -0.047610  0.006123 -0.000881 -0.004941  0.001822 -0.005707  
2014-01-08 -0.003877  0.000218 -0.003016 -0.004705 -0.016522 -0.005909

In [11]:
rets.mean() * 252  # annualized, average log returns

AAPL.O    0.228139
MSFT.O    0.231906
INTC.O    0.066835
AMZN.O    0.203688
GS.N      0.078126
.SPX      0.095882
.VIX     -0.013390
SPY       0.095682
EUR=     -0.021447
XAU=      0.052246
GDX       0.034258
GLD       0.048344
dtype: float64

In [15]:
np.exp(rets.mean() * 252) - 1  # annualized, average simple returns

AAPL.O    0.256260
MSFT.O    0.261002
INTC.O    0.069119
AMZN.O    0.225916
GS.N      0.081259
.SPX      0.100629
.VIX     -0.013301
SPY       0.100409
EUR=     -0.021218
XAU=      0.053635
GDX       0.034852
GLD       0.049531
dtype: float64

### Plotting the Data

`pip install cufflinks`

In [16]:
data.normalize().iplot(kind='lines')

In [20]:
rets.iplot(kind='histogram', subplots=True)  # none of the return plots are fully normal

In [18]:
rets.corr()

AAPL.O    MSFT.O    INTC.O    AMZN.O      GS.N      .SPX      .VIX  \
AAPL.O  1.000000  0.671831  0.516156  0.543314  0.476955  0.743972 -0.531499   
MSFT.O  0.671831  1.000000  0.579924  0.620873  0.490615  0.791860 -0.578771   
INTC.O  0.516156  0.579924  1.000000  0.408150  0.460086  0.658014 -0.480425   
AMZN.O  0.543314  0.620873  0.408150  1.000000  0.363688  0.613486 -0.476619   
GS.N    0.476955  0.490615  0.460086  0.363688  1.000000  0.746225 -0.550598   
.SPX    0.743972  0.791860  0.658014  0.613486  0.746225  1.000000 -0.727456   
.VIX   -0.531499 -0.578771 -0.480425 -0.476619 -0.550598 -0.727456  1.000000   
SPY     0.744778  0.787796  0.653088  0.614387  0.747531  0.997238 -0.727570   
EUR=    0.042742  0.030193  0.029807  0.058994  0.048401  0.079628 -0.015543   
XAU=    0.005467  0.001011  0.025921  0.018163 -0.107959  0.004257  0.047934   
GDX     0.089551  0.104762  0.106360  0.108897  0.057176  0.164041 -0.102703   
GLD     0.014880  0.011805  0.040658  0.023105 -0.099730  0.018071  0.037400   

             SPY      EUR=      XAU=       GDX       GLD  
AAPL.O  0.744778  0.042742  0.005467  0.089551  0.014880  
MSFT.O  0.787796  0.030193  0.001011  0.104762  0.011805  
INTC.O  0.653088  0.029807  0.025921  0.106360  0.040658  
AMZN.O  0.614387  0.058994  0.018163  0.108897  0.023105  
GS.N    0.747531  0.048401 -0.107959  0.057176 -0.099730  
.SPX    0.997238  0.079628  0.004257  0.164041  0.018071  
.VIX   -0.727570 -0.015543  0.047934 -0.102703  0.037400  
SPY     1.000000  0.084090  0.001334  0.166305  0.015061  
EUR=    0.084090  1.000000  0.377736  0.320719  0.377719  
XAU=    0.001334  0.377736  1.000000  0.760086  0.986020  
GDX     0.166305  0.320719  0.760086  1.000000  0.763609  
GLD     0.015061  0.377719  0.986020  0.763609  1.000000

In [22]:
rets.corr().iplot(kind='heatmap', colorscale='reds')
# only VIX really has negative correlations to the other assets
# on the main diagonal fully correlated (with itself)

### Preparing Lagged Data

In [23]:
def add_lags(data, ric, lags):  # lag the pricing data by trading day (not calendar day)
    cols = []
    df = pd.DataFrame(data[ric])
    for lag in range(1, lags + 1):
        col = 'lag_{}'.format(lag)  # defines the column name
        df[col] = df[ric].shift(lag)  # creates the lagged data column
        cols.append(col)  # stores the column name
    df.dropna(inplace=True)  # gets rid of incomplete data rows
    return df, cols

In [24]:
lags = 7  # seven historical lags

In [25]:
dfs = {}
for sym in data.columns:
    df, cols = add_lags(data, sym, lags)
    dfs[sym] = df

In [26]:
cols  # the column names for the lags

['lag_1', 'lag_2', 'lag_3', 'lag_4', 'lag_5', 'lag_6', 'lag_7']

In [27]:
dfs.keys()  # the keys of the dictonary

dict_keys(['AAPL.O', 'MSFT.O', 'INTC.O', 'AMZN.O', 'GS.N', '.SPX', '.VIX', 'SPY', 'EUR=', 'XAU=', 'GDX', 'GLD'])

In [29]:
dfs['AAPL.O'].head(7)
# lag_1 is AAPL date from 1 day before. Can see how "today" (lag_0) price is moving on the diagonal downwards

AAPL.O      lag_1      lag_2      lag_3      lag_4      lag_5  \
Date                                                                           
2014-01-13  19.133195  19.033552  19.161374  19.409266  19.287034  19.426052   
2014-01-14  19.513909  19.133195  19.033552  19.161374  19.409266  19.287034   
2014-01-15  19.905694  19.513909  19.133195  19.033552  19.161374  19.409266   
2014-01-16  19.794623  19.905694  19.513909  19.133195  19.033552  19.161374   
2014-01-17  19.309624  19.794623  19.905694  19.513909  19.133195  19.033552   
2014-01-21  19.609623  19.309624  19.794623  19.905694  19.513909  19.133195   
2014-01-22  19.696766  19.609623  19.309624  19.794623  19.905694  19.513909   

                lag_6      lag_7  
Date                              
2014-01-13  19.320695  19.754623  
2014-01-14  19.426052  19.320695  
2014-01-15  19.287034  19.426052  
2014-01-16  19.409266  19.287034  
2014-01-17  19.161374  19.409266  
2014-01-21  19.033552  19.161374  
2014-01-22  19.133195  19.033552

### Implementing OLS Regression

In [30]:
regs = {}
for sym in data.columns:
    df = dfs[sym]  # getting data for the RIC
    reg = np.linalg.lstsq(df[cols], df[sym], rcond=-1)[0]  # the OLS regression
    regs[sym] = reg  # storing the results

In [31]:
np.set_printoptions(suppress=True)

In [32]:
for sym in data.columns:
    print('{:10} | {}'.format(sym, regs[sym].round(4)))

AAPL.O     | [ 0.962   0.0128  0.0105  0.0096  0.0414 -0.0529  0.0173]
MSFT.O     | [ 0.8922  0.0748 -0.0026  0.0402  0.0246 -0.1003  0.0722]
INTC.O     | [ 0.855   0.2115 -0.0284 -0.0662  0.0194 -0.0415  0.0503]
AMZN.O     | [ 0.9763  0.0309 -0.0452  0.072  -0.046   0.0118  0.0005]
GS.N       | [ 1.0224  0.0137 -0.0443 -0.0139  0.0203  0.0149 -0.0131]
.SPX       | [ 0.9126  0.1316 -0.0581 -0.0274  0.0611 -0.0968  0.0774]
.VIX       | [ 0.8316  0.182   0.0176 -0.114   0.0707 -0.0296  0.0382]
SPY        | [ 0.9265  0.1057 -0.0438 -0.0274  0.0582 -0.0921  0.0732]
EUR=       | [ 0.988   0.007  -0.0231  0.0466 -0.016  -0.0742  0.0715]
XAU=       | [ 1.0085 -0.0419  0.057  -0.0198 -0.027   0.0145  0.0088]
GDX        | [ 0.9601 -0.0072  0.0528 -0.0109 -0.0284  0.0241  0.0094]
GLD        | [ 1.0103 -0.0489  0.0578 -0.0145 -0.0244  0.0048  0.0151]


In [33]:
rega = np.stack(tuple(regs.values()))  # combines the regression results

In [34]:
rega.mean(axis=0)  # mean values by column

array([ 0.94545439,  0.05599816, -0.00415154, -0.01046992,  0.01283497,
       -0.03477922,  0.0350721 ])

In [35]:
regd = pd.DataFrame(rega, columns=cols, index=data.columns)  # converting the results to DataFrame

In [36]:
regd

lag_1     lag_2     lag_3     lag_4     lag_5     lag_6     lag_7
AAPL.O  0.961962  0.012802  0.010513  0.009615  0.041400 -0.052910  0.017311
MSFT.O  0.892192  0.074755 -0.002608  0.040179  0.024554 -0.100348  0.072187
INTC.O  0.855008  0.211477 -0.028434 -0.066216  0.019425 -0.041541  0.050300
AMZN.O  0.976268  0.030916 -0.045208  0.071967 -0.046014  0.011833  0.000496
GS.N    1.022434  0.013737 -0.044266 -0.013898  0.020349  0.014900 -0.013057
.SPX    0.912641  0.131603 -0.058126 -0.027384  0.061113 -0.096833  0.077386
.VIX    0.831566  0.182023  0.017570 -0.113997  0.070705 -0.029602  0.038195
SPY     0.926465  0.105741 -0.043760 -0.027402  0.058229 -0.092093  0.073213
EUR=    0.988026  0.006977 -0.023073  0.046624 -0.016026 -0.074174  0.071527
XAU=    1.008453 -0.041905  0.056979 -0.019763 -0.026960  0.014547  0.008848
GDX     0.960109 -0.007215  0.052761 -0.010854 -0.028355  0.024113  0.009351
GLD     1.010328 -0.048933  0.057833 -0.014510 -0.024402  0.004757  0.015109

In [39]:
regd.iplot(kind='bar')  # lag_1 has highest weight

In [40]:
regd.mean().iplot(kind='bar')  # lag_1 completely dominates

## Another Approach

In [41]:
import statsmodels.api as sm

In [42]:
x_ = sm.add_constant(df[cols[:]], prepend=False)

In [43]:
y = df[sym]

In [44]:
mod = sm.OLS(y, x_)
reg = mod.fit()

In [45]:
reg.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                    GLD   R-squared:                       0.998
Model:                            OLS   Adj. R-squared:                  0.998
Method:                 Least Squares   F-statistic:                 1.452e+05
Date:                Fri, 07 Jun 2024   Prob (F-statistic):               0.00
Time:                        21:52:02   Log-Likelihood:                -4221.2
No. Observations:                2509   AIC:                             8458.
Df Residuals:                    2501   BIC:                             8505.
Df Model:                           7                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
lag_1          1.0101      0.020     50.538      0.000       0.971       1.049
lag_2         -0.0489      0.028     -1.722      0.085      -0.105       0.007
lag_3          0.0578      0.028      2.034      0.042       0.002       0.114
lag_4         -0.0145      0.028     -0.510      0.610      -0.070       0.041
lag_5         -0.0244      0.028     -0.859      0.390      -0.080       0.031
lag_6          0.0047      0.028      0.167      0.867      -0.051       0.060
lag_7          0.0147      0.020      0.733      0.464      -0.025       0.054
const          0.1067      0.142      0.750      0.453      -0.172       0.386
==============================================================================
Omnibus:                      287.641   Durbin-Watson:                   2.001
Prob(Omnibus):                  0.000   Jarque-Bera (JB):             2184.687
Skew:                          -0.250   Prob(JB):                         0.00
Kurtosis:                       7.544   Cond. No.                     2.07e+03
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 2.07e+03. This might indicate that there are
strong multicollinearity or other numerical problems.
"""

## Cross Check

In [46]:
sym = 'AAPL.O'

In [47]:
reg = regd.loc[sym].values

In [48]:
y_ = np.dot(dfs[sym][cols], reg)  # predictions

In [49]:
r = y_ - dfs[sym][sym]  # residuals

Check for assumptions:
* **linearity**: given
* **independence**: <b style="color: red;">not at all</b>
* **zero mean**: somehow
* **no correlation**: given
* **homoscedasticity**: <b>given</b>
* **no autocorrelation**: given
* **stationarity**: <b style="color: red;">not given</b>

In [63]:
dfs[sym][cols].corr()  # lags highly correlated
# --> conditions are violated, but lag_1 is enough to build prediction model on

lag_1     lag_2     lag_3     lag_4     lag_5     lag_6     lag_7
lag_1  1.000000  0.999523  0.999082  0.998664  0.998259  0.997858  0.997422
lag_2  0.999523  1.000000  0.999523  0.999081  0.998663  0.998257  0.997856
lag_3  0.999082  0.999523  1.000000  0.999522  0.999080  0.998661  0.998255
lag_4  0.998664  0.999081  0.999522  1.000000  0.999522  0.999079  0.998660
lag_5  0.998259  0.998663  0.999080  0.999522  1.000000  0.999521  0.999078
lag_6  0.997858  0.998257  0.998661  0.999079  0.999521  1.000000  0.999520
lag_7  0.997422  0.997856  0.998255  0.998660  0.999078  0.999520  1.000000

In [65]:
r.mean()  # residuals (real value minus predicted value) is close to 0

-0.019749117386316774

In [52]:
np.corrcoef(r, dfs[sym]['lag_3'])

array([[1.        , 0.01583544],
       [0.01583544, 1.        ]])

In [53]:
from scipy.stats import bartlett

In [66]:
split = int(len(dfs) / 2)

In [68]:
bartlett(r[:split], r[split:])  # low p-value --> can reject H0 zero hypothesis

BartlettResult(statistic=10.884008936766744, pvalue=0.0009699806830879944)

In [69]:
from statsmodels.graphics.tsaplots import plot_acf

In [71]:
fig, ax = plt.subplots(figsize=(10, 6))
plot_acf(r, ax=ax);  # plot shows almost not auto-correlated

In [58]:
from statsmodels.tsa.stattools import adfuller

In [72]:
# adfuller test: needs to be below -2.567 to be stationary. Let's test...

In [76]:
adfuller(dfs[sym][sym])  # the first value of tuple 0.2674101382547608 > -2.567, is too high! --> prices are not stationary

(0.2674101382547608,
 0.9757988715840423,
 18,
 2490,
 {'1%': -3.4329789374204935,
  '5%': -2.8627014485379787,
  '10%': -2.5673882843825098},
 9785.716862572648)

In [80]:
# look at simple returns now:
adfuller(dfs[sym][sym].pct_change().dropna())  # -15.913446018933918 < -2.567 --> percentage change (returns) are stationary
# if we re-did the whole tests (From Cross Check on for the pct_change(), no assumptions would be violated, no red flags),
# i.e. returns are independent and stationary

(-15.913446018933918,
 8.074494619164124e-29,
 8,
 2499,
 {'1%': -3.4329694597063978,
  '5%': -2.8626972631809684,
  '10%': -2.567386056042265},
 -12968.004509415241)

<img src="http://hilpisch.com/tpq_logo.png" alt="The Python Quants" width="35%" align="right" border="0"><br><br>

 <a href="mailto:training@tpq.io">training@tpq.io</a> | https://cpf.tpq.io | [@dyjh](http://twitter.com/dyjh) | [YouTube](http://youtube.com/@dyjh)